# Handling Earthquake data from USGS with PySpark

In this project I'm getting my hands on PySpark to explore and clean data from the USGS to get to know PySpark better. I'm also exploring when to use 'to_Koalas()' vs 'toPandas()'. Additonally, I'm using PySpark's MLlib for clustering earthquaks by location. Here it turned out that MLlib's distance-based clustering models only support euclidean or cosine as distance measure. To accomodate for the earths spherical shape, I had to do a little dive into geostatstics. In the end, sklearn's DBSCAN with haversine distance produced a good result. 

In [1]:
import requests
import pandas as pd
import io

import findspark
from pyspark.sql import SparkSession
from pyspark import SparkContext
from pyspark.sql import SQLContext

In [2]:
start_time = '2019-01-01'
end_time = '2019-12-31'
min_magnitude = '3.0'


In [3]:
def get_data(start_date, end_date, min_magnitude):
    
    url = 'https://earthquake.usgs.gov/fdsnws/event/1/query?format=csv&starttime={}&endtime={}&minmagnitude={}'\
    .format(start_date,end_date,min_magnitude)
    response = requests.get(url).content
    df_get_data = spark.createDataFrame(pd.read_csv(io.StringIO(response.decode('utf-8'))))
    
    return df_get_data

In [4]:
findspark.init()

spark = SparkSession.builder.getOrCreate()
sc = spark.sparkContext
sqlContext = SQLContext(sc)


In [5]:
df = get_data(start_time, end_time, min_magnitude)

##### Hint : To get a nice presentation of Pyspark's '.show()' in the notebook, please change the CSS value of 'white-space' to 'pre'. To do so open developer mode in your browser, select the element where a df is displayed.

In [7]:
df.show(10)

+--------------------+--------+---------+------+----+-------+---+-----+-------------------+----+---+------------+--------------------+--------------------+----------------+---------------+----------+--------------------+------+--------+--------------+---------+
|                time|latitude|longitude| depth| mag|magType|nst|  gap|               dmin| rms|net|          id|             updated|               place|            type|horizontalError|depthError|            magError|magNst|  status|locationSource|magSource|
+--------------------+--------+---------+------+----+-------+---+-----+-------------------+----+---+------------+--------------------+--------------------+----------------+---------------+----------+--------------------+------+--------+--------------+---------+
|2019-12-30T22:37:...|  19.436| -66.2138|  33.0|3.16|     md|9.0|310.0|             1.1345|0.26| pr|pr2019364036|2020-03-14T22:23:...|95km N of Brenas,...|      earthquake|           2.15|     17.27|               

In [10]:
print('Row count: ', df.count())
print('Number of distinct Places: ', df.select('place').distinct().count())

Row count:  18129
Number of distinct Places:  13703


### Inspecting the 'place' column

In [18]:
places = df.groupby('place').count()
                                              
places.orderBy('count', ascending = False).show(5,truncate = False)

+---------------------------+-----+
|place                      |count|
+---------------------------+-----+
|South of the Fiji Islands  |267  |
|Wyoming                    |136  |
|Izu Islands, Japan region  |83   |
|Northern Mid-Atlantic Ridge|73   |
|Carlsberg Ridge            |60   |
+---------------------------+-----+
only showing top 5 rows



In [15]:
df.describe().show()

+-------+--------------------+------------------+-------------------+------------------+-----------------+-------+-----+-----+-----+-------------------+-----+------------+--------------------+--------------------+-----------+---------------+-----------------+--------+------+---------+--------------+---------+
|summary|                time|          latitude|          longitude|             depth|              mag|magType|  nst|  gap| dmin|                rms|  net|          id|             updated|               place|       type|horizontalError|       depthError|magError|magNst|   status|locationSource|magSource|
+-------+--------------------+------------------+-------------------+------------------+-----------------+-------+-----+-----+-----+-------------------+-----+------------+--------------------+--------------------+-----------+---------------+-----------------+--------+------+---------+--------------+---------+
|  count|               18129|             18129|              1812

### Checking for missing values

In [12]:
from pyspark.sql.functions import isnan, when, count, col

In [13]:
df.select([count(when(isnan(c), c)).alias(c) for c in df.columns]).show()


+----+--------+---------+-----+---+-------+-----+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+
|time|latitude|longitude|depth|mag|magType|  nst|gap|dmin|rms|net| id|updated|place|type|horizontalError|depthError|magError|magNst|status|locationSource|magSource|
+----+--------+---------+-----+---+-------+-----+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+
|   0|       0|        0|    0|  0|      0|15339|738| 768|  0|  0|  0|      0|    0|   0|            808|         0|    1157|   902|     0|             0|        0|
+----+--------+---------+-----+---+-------+-----+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+



In [14]:
df.select([count(when(col(c).isNull(), c)).alias(c) for c in df.columns]).show()


+----+--------+---------+-----+---+-------+---+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+
|time|latitude|longitude|depth|mag|magType|nst|gap|dmin|rms|net| id|updated|place|type|horizontalError|depthError|magError|magNst|status|locationSource|magSource|
+----+--------+---------+-----+---+-------+---+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+
|   0|       0|        0|    0|  0|      0|  0|  0|   0|  0|  0|  0|      0|    0|   0|              0|         0|       0|     0|     0|             0|        0|
+----+--------+---------+-----+---+-------+---+---+----+---+---+---+-------+-----+----+---------------+----------+--------+------+------+--------------+---------+



Since the majority of rows have a NaN value for 'nst' it get's dropped. From USGS 'nst' is : INSERT INSERT

In [14]:
df = df.drop('nst')

#### Value counts of 'type' column

In [17]:
types = df.groupby('type').count()
types.show()

+----------------+-----+
|            type|count|
+----------------+-----+
|mining explosion|  154|
|      earthquake|17974|
|     other event|    1|
+----------------+-----+



#### Making sure only earthquakes that are reviewed are in the df

In [20]:
eq = df.filter((df.type == 'earthquake') & (df.status == 'reviewed'))
eq.count()

17966

## Depth and Magnitude

#### USGS on the relationship between depth and magnitude of an earthquake: 
##### 'The strength of shaking from an earthquake diminishes with increasing distance from the earthquake's source, so the strength of shaking at the surface from an earthquake that occurs at 500km deep is considerably less than if the same earthquake had occurred at 20 km depth.'

#### So let's take a closer look at the 'depth' and 'mag' column and see if this relationship also applies to our sample.

### Depth 

In [141]:
eq.select(eq['depth']).describe().show()

+-------+------------------+
|summary|             depth|
+-------+------------------+
|  count|             17966|
|   mean| 76.11846209506842|
| stddev|130.04816929836946|
|    min|             -3.34|
|    max|            667.39|
+-------+------------------+



#### Huh, earthquakes with a negative depth? According to the USGS, these values are the result of earthquakes occuring at a very low depth, and an error of a few kilometers.  So let's keep those very shallow earthquakes in the df for now. 

In [23]:
e = eq.filter(eq['depth'] <= 0)
print('Number of earthquakes with a depth of zero or negative: ', e.count())

Number of earthquakes with a depth of 0 or smaller:  21


In [25]:
import plotly.express as px
fig = px.histogram(eq.toPandas(), x="depth", nbins = 100)
fig.show()


#### We see that a very high amount of earthquakes falls into the second bin (5-14.99), again USGS provides an explanation for that: 

##### "Sometimes when depth is poorly constrained by available seismic data, the location program will set the depth at a fixed value. For example, 33 km is often used as a default depth for earthquakes determined to be shallow, but whose depth is not satisfactorily determined by the data, whereas default depths of 5 or 10 km are often used in mid-continental areas and on mid-ocean ridges since earthquakes in these areas are usually shallower than 33 km."

#### The USGS also provides a threshold for classifiying earthquakes based on their depth into 'shallow' ( depth <= 70) and 'deep-focus'. Let's create a new column to group our earthquakes.

In [29]:
from pyspark.sql.functions import when

In [30]:
#### grouping into shallow, intermediate and 
eq = eq.withColumn('depth_class', when(eq.depth <= 70, 'shallow') ## 'shallow'
                                 .otherwise('deep-focus')         ## 'deep-focus'
             )

In [31]:
eq.crosstab('depth_class', 'mag').show()

+---------------+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+---+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+----+---+----+----+----+----+---+----+----+----+----+---+----+----+----+---+----+---+---+----+---+----+----+---+----+---+----+----+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---+---

# Removing high error outliers

#### There are three columns that measure the error for magnitude, depth, and location. Let's remove rows that have exceptionally high error values in one of these clolumns.

In [45]:
import databricks.koalas as ks
import os
os.environ["PYARROW_IGNORE_TIMEZONE"] = "1"

In [46]:
def get_threshold(column):
    q1 = column.quantile(0.25)
    q3 = column.quantile(0.75)
    iqr = q3 - q1
    threshold = q3 +(1.5*iqr)
    return threshold

In [47]:
kdf = eq.to_koalas()

In [48]:
kdf.head(2)

time  latitude  longitude  depth   mag magType  nst    gap    dmin   rms net            id                   updated                          place        type  horizontalError  depthError  magError  magNst    status locationSource magSource depth_class
0  2019-12-30T22:37:00.570Z   19.4360   -66.2138  33.00  3.16      md  9.0  310.0  1.1345  0.26  pr  pr2019364036  2020-03-14T22:23:01.040Z  95km N of Brenas, Puerto Rico  earthquake             2.15       17.27     0.130     6.0  reviewed             pr        pr     shallow
1  2019-12-30T22:00:10.704Z   43.9087  -111.0947   7.51  3.10      ml  NaN   83.0  0.2750  0.32  us    us70006spn  2020-03-14T22:23:02.040Z        20km N of Driggs, Idaho  earthquake             1.00        4.50     0.059    38.0  reviewed             us        us     shallow

## Dmin

##### USGS : "In general, the smaller this number, the more reliable is the calculated depth of the earthquake."

In [49]:
fig = px.box(eq.toPandas(), x="dmin")
fig.show()

In [50]:
thresh_dmin = get_threshold(kdf['dmin'])
thresh_dmin

8.52845

### magError

In [51]:
fig = px.box(eq.toPandas(), x='magError')
fig.show()

In [54]:
thresh_magError = get_threshold(kdf['magError'])
thresh_magError

0.30500000000000005

### Horizontal Error

In [55]:
fig = px.box(eq.toPandas(), x='horizontalError')
fig.show()

In [56]:
thresh_horizontalError = get_threshold(kdf['horizontalError'])
thresh_horizontalError

18.48

In [64]:
eq2 = eq.filter((eq.dmin <= thresh_dmin) & (eq.magError <= thresh_magError) & (eq.magError <= thresh_horizontalError))

In [65]:
print('Number of rows BEFORE dropping dmin & magError outliers: ', eq.count())
print('Number of rows AFTER dropping dmin & magError outliers: ', eq2.count())

Number of rows BEFORE dropping dmin & magError outliers:  17966
Number of rows AFTER dropping dmin & magError outliers:  15187


### Exploring different ways to get the average magnitude per depth_class

In [66]:
eq2.createOrReplaceTempView("eq2")
%alias_magic t timeit

Created `%t` as an alias for `%timeit`.
Created `%%t` as an alias for `%%timeit`.


#### SQL Query

In [67]:
%timeit -r 1 -n 1 spark.sql('SELECT ROUND(AVG(mag),2) AS Deep_Focus_Earthquake_avg_magnitude FROM eq2 WHERE depth_class = "deep-focus"').show()

+-----------------------------------+
|Deep_Focus_Earthquake_avg_magnitude|
+-----------------------------------+
|                               4.35|
+-----------------------------------+

7.61 s ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


### .filter()


In [68]:
import pyspark.sql.functions as F

In [71]:
%timeit -r 1 -n 1 eq2.filter(eq2['depth_class'] == 'shallow').agg(F.round(F.avg(eq2['mag']),2).alias('Shallow Earthquake avg magnitude')).show()


+--------------------------------+
|Shallow Earthquake avg magnitude|
+--------------------------------+
|                            4.27|
+--------------------------------+

6.91 s ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


### GroupBy()


In [72]:
%timeit -r 1 -n 1 eq2.groupBy('depth_class').agg(F.round(F.avg('mag'),2).alias('avg magnitude')).show()


+-----------+-------------+
|depth_class|avg magnitude|
+-----------+-------------+
| deep-focus|         4.35|
|    shallow|         4.27|
+-----------+-------------+

7.52 s ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


### Exploring relationship between variables

In [78]:
from pyspark.ml.stat import Correlation
from pyspark.mllib.stat import Statistics


In [99]:
df = eq2.select('mag','depth','longitude','latitude')

In [85]:
# https://gist.github.com/cameres/bc24ac6711c9e537dd20be47b2a83558
def compute_correlation_matrix(df, method='pearson'):
    
    df_rdd = df.rdd.map(lambda row: row[0:])
    corr_mat = Statistics.corr(df_rdd, method=method)
    corr_mat_df = pd.DataFrame(corr_mat,
                    columns=df.columns, 
                    index=df.columns)
    return corr_mat_df

In [87]:
compute_correlation_matrix(df, method='pearson')

mag     depth  longitude  latitude      dmin
mag        1.000000  0.075357   0.364029 -0.413832  0.345246
depth      0.075357  1.000000  -0.114905 -0.295752  0.260881
longitude  0.364029 -0.114905   1.000000  0.008276  0.142068
latitude  -0.413832 -0.295752   0.008276  1.000000 -0.315863
dmin       0.345246  0.260881   0.142068 -0.315863  1.000000

No correlation between depth and magnitude in the sample

In [93]:
depth_class = eq2.select('depth_class', 'depth','mag').toPandas()

In [97]:
fig = px.scatter(depth_class, x='depth', y='mag', color='depth_class')
fig.show()

In [98]:
depth_class['depth_class'].value_counts()

shallow       10867
deep-focus     4320
Name: depth_class, dtype: int64

#### For this sample we can't make the observation that depth is an indicator for the magnitude of an earthquake. We know from the USGS that deeper earthquakes tend to have a smaller magnitude on the surface compared to shallower earthquakes. Since we originally set the minimum magnitude at 3, the sample inlcudes more shallow earthquakes. 
#### Also we should consider that shallow earthquakes are easier to detect, and that some deep earthquakes might not even get picked up by measuring stations.

In [100]:
fig = px.scatter(df.toPandas(), x='longitude', y= 'latitude')
fig.show()

                                                    Looks familiar doesn't it?

### Clustering

#### On first glance this looks like a good opportunity to try out PySpark's clustering algorithms. However, the world is not flat and it is doubtful that k-means with eucledian distance will give us the best result. 

##### "K-means minimizes variance, not geodetic distance" - https://geoffboeing.com/2014/08/clustering-to-reduce-spatial-data-set-size/

#### Ideally we would be using an algorithm that can handle haversine distance, which allows us to accurately calculate the distance between points on a sphere. But since I would like to experiment with the ml library a little I will compare PySpark's Bisecting k-means that uses a 'kind of hierarchical top-down' approach with DBSCAN. DBSCAN which is commonly suggested for clustering spatial data is not included in the PySpark's ml library.


In [101]:
from pyspark.ml.feature import VectorAssembler


In [102]:
assemble = VectorAssembler(inputCols = ['longitude','latitude'], outputCol = 'features')

In [103]:
assembled_data = assemble.transform(df)


In [105]:
from pyspark.ml.feature import StandardScaler
scale=StandardScaler(inputCol='features',outputCol='standardized')
data_scale=scale.fit(assembled_data)
data_scale_output=data_scale.transform(assembled_data)
data_scale_output.show(2)

+----+-----+---------+--------+-------------------+--------------------+
| mag|depth|longitude|latitude|           features|        standardized|
+----+-----+---------+--------+-------------------+--------------------+
|3.16| 33.0| -66.2138|  19.436|  [-66.2138,19.436]|[-0.5181423743746...|
| 3.1| 7.51|-111.0947| 43.9087|[-111.0947,43.9087]|[-0.8693485593401...|
+----+-----+---------+--------+-------------------+--------------------+
only showing top 2 rows



In [107]:
from pyspark.ml.clustering import KMeans
from pyspark.ml.clustering import BisectingKMeans
from pyspark.ml.evaluation import ClusteringEvaluator
silhouette_score=[]
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='standardized', \
                                metricName='silhouette', distanceMeasure='squaredEuclidean')

#### Determining k for Bisecting K-Means

In [108]:
### Determining k for k-means with silhouette score from towardsdatascience
### https://towardsdatascience.com/k-means-clustering-using-pyspark-on-big-data-6214beacdc8b#:

for i in range(2,12):
    
    bkm_algo=BisectingKMeans(featuresCol='standardized', k=i)
    
    bkm_fit=bkm_algo.fit(data_scale_output)           ##### data_scale_output 
    
    output=bkm_fit.transform(data_scale_output)   ### data_scale_output
    
    
    
    score=evaluator.evaluate(output)
    
    silhouette_score.append(score)
    
    print("Silhouette Score:",score)

Silhouette Score: 0.6172749780837058
Silhouette Score: 0.564063836519272
Silhouette Score: 0.7669112045155405
Silhouette Score: 0.7168883893970609
Silhouette Score: 0.6878856633533287
Silhouette Score: 0.6808965075298905
Silhouette Score: 0.6045800059613899
Silhouette Score: 0.5092776538810204
Silhouette Score: 0.5312176166381863
Silhouette Score: 0.5846592031927376


In [109]:
line = px.line(x=range(2,12), y = silhouette_score )
line.update_layout(width = 600, height = 400, yaxis = dict(title = 'cost'), xaxis = dict(title = 'k'))
line.show()


### K-Means

In [391]:
KMeans_algo=KMeans(featuresCol='standardized', k=4)
    
KMeans_fit=KMeans_algo.fit(data_scale_output)
    
output=KMeans_fit.transform(data_scale_output)

score=evaluator.evaluate(output)


In [392]:
centers = KMeans_fit.clusterCenters()
centers

[array([ 1.03538034, -0.15091217]),
 array([-0.84045909,  1.16778765]),
 array([-1.02360573, -0.9292624 ]),
 array([0.86127601, 1.36334389])]

## BiSecting K-Means

In [110]:
bkm_algo=BisectingKMeans(featuresCol='standardized', k=4)
    
bkm_fit=bkm_algo.fit(data_scale_output)           ##### data_scale_output 
    
output=bkm_fit.transform(data_scale_output)   ### data_scale_output
    

### Determining cluster centers, reverse standardization

In [111]:
centers = []

In [112]:
for cluster in bkm_fit.clusterCenters():   ### KMeans_fit
    e = cluster * data_scale.std 
    centers.append(e)

In [113]:
centers

[array([-129.57191806,  -24.75508085]),
 array([-110.4297985 ,   33.32101852]),
 array([131.48046746,  -4.08488999]),
 array([109.72952771,  36.89751155])]

In [118]:
df_centers = pd.DataFrame.from_records(centers)
df_centers = df_centers.rename(columns = {0:'longitude', 1:'latitude'})

In [119]:
df_centers.head()

longitude   latitude
0 -129.571918 -24.755081
1 -110.429799  33.321019
2  131.480467  -4.084890
3  109.729528  36.897512

In [120]:
output.show(2)

+----+-----+---------+--------+-------------------+--------------------+----------+
| mag|depth|longitude|latitude|           features|        standardized|prediction|
+----+-----+---------+--------+-------------------+--------------------+----------+
|3.16| 33.0| -66.2138|  19.436|  [-66.2138,19.436]|[-0.5181423743746...|         1|
| 3.1| 7.51|-111.0947| 43.9087|[-111.0947,43.9087]|[-0.8693485593401...|         1|
+----+-----+---------+--------+-------------------+--------------------+----------+
only showing top 2 rows



In [121]:
output_vis = output.select('longitude','latitude','prediction').toPandas()

In [124]:
fig = go.Figure(data=go.Scattergeo(
        lon = output_vis['longitude'],
        lat = output_vis['latitude'],
        text = output_vis['prediction'],
        mode = 'markers',
        name= 'Earthquakes',
        marker_color = output_vis['prediction'],
        ))

fig.add_scattergeo(

                         lon=df_centers['longitude'],
                         lat=df_centers['latitude'],
                         mode = 'markers',
                         name= 'Cluster centers',
            
                         #text = output_vis['prediction'],
                         marker = dict(color = '#7DF700',
                         size = 16,
                         line = dict(width=2, color = '#262626' ))


)


fig.show()

#### As expected the result doesn't take into consideration the shape of the earth. In the Pacific, we can clearly see the limitations of this method. So let's see if that can be improved with DBSCAN

### DBSCAN
##### kudos to Geoff Boeing https://github.com/gboeing/2014-summer-travels/blob/master/clustering-scikitlearn.ipynb

In [125]:
from sklearn.cluster import DBSCAN
from geopy.distance import great_circle
from shapely.geometry import MultiPoint
import numpy as np

In [131]:
df = df[['latitude','longitude']].toPandas()

In [134]:
coords = df.to_numpy()

In [262]:
kms_per_radian = 6371.0088
epsilon = 400 / kms_per_radian
epsilon

0.06278440550890466

In [263]:
#### ganz ok epsilon 500, min_samples = 70
#### besser mit 180 grad epsilon 600, min_samples = 70
#### noch besser 600 epsilon, min_samples 40
#### detailed 400 epsilon min_samples 40
#### best 33 

In [264]:
db = DBSCAN(eps=epsilon, min_samples=33, algorithm='ball_tree', metric='haversine').fit(np.radians(coords)) #


#### By setting min_samples not to 1, we accept that there will be outliers. Earthquakes that won't be assigned to a cluster. 

In [265]:
cluster_labels = db.labels_
num_clusters = len(set(cluster_labels))
clusters = pd.Series([coords[cluster_labels == n] for n in range(num_clusters)])
print('Number of clusters: {}'.format(num_clusters))


Number of clusters: 15


In [266]:
df['cluster'] = cluster_labels

In [267]:
df['cluster'].value_counts()

 2     7308
 5     1910
 7     1503
 1     1344
-1      828
 0      820
 4      365
 3      295
 10     193
 6      192
 9      181
 13      83
 8       70
 11      62
 12      33
Name: cluster, dtype: int64

#### clusters labeled -1 are outliers

In [268]:
fig = go.Figure(data=go.Scattergeo(
        lon = df['longitude'],
        lat = df['latitude'],
        text = df['cluster'],
        mode = 'markers',
        name= 'Earthquakes',
        marker_color = df['cluster'],
        marker = dict(colorscale = 'fall'),  

        ))




fig.show()

####  Compared to (Bisecting) K-Means, DBSCAN provides more accurate clusters that are geographically distinct. For example, in the USA it can be clearly disntinguished between the Pacific west coast cluster, a central cluster in South Carolina, and Hawaii.

#### Instead of just relying on k as input, DBSCAN allows us to determine the minimum number of samples(that have to make up a cluster) and epsilon (max distance between two points in the same cluster). This gives us more control over the shape and size of the clusters. 

#### Take a look at the pacific ring of fire: https://cdn.britannica.com/57/5457-050-84F0FBED/ring-volcanoes-arcs-tectonic-plate-boundaries-Pacific.jpg

#### As epsilon increases, the number of clusters (e.g. along the pacific ring of fire) decreases as well as the number of outliers. So it depends on what number of outliers is deemed as acceptable, and what the desired size of clusters is. It's also possible to reduce the number of outliers and maintain the epsilon value, by adjusting the 'min_samples' parameter. 

#### Another benefit of DBSCAN can be observed in the bering sea. Thanks to the density based approach and the use of haversine distance measure, we get a nice big cluster that spans the globe, and connects Russia and Alaska. As we saw before, k-means with euclidean distance measure would have cut of that cluster into eastern and western hemisphere - without taking into account the spherical shape.

